# Homework 3

# Task 1 (No coding, ura!)

# Task 2 (Coding)

You should find:
1. simulate this mechanism (obtain all positions);
2. Find absolute, transport and relative velocities and accelerations for M;
3. Find t, when M reaches O point;
4. draw plots $v_rel, v_tr, a_tr, a_rel, a$ respect to time.

Needed variables:
$\phi_e = f_1(t) = 0.2t^3 + t;$
$OM = s_r = f_2(t) = 5\sqrt2(t^2 + t)$
$a = 60, α = 45.$


In [4]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from sympy import solve, diff, sin, cos, lambdify, sqrt
from sympy.abc import symbols
from IPython.display import HTML, display

num_frames = 120
t_start = 0
t_end = 3
t_values = np.linspace(t_start, t_end, num_frames)

O1O = 60
alpha = np.radians(45)

# Set the needed variables for further solving using sympy
t, phi, x_M, y_M, k_OO2, b_OO2, px1, px2, py1, py2, k, b, O1M, OM, O1M1 = symbols('t, phi, x_M, y_M, k_OO2, b_OO2, px1, px2, py1, py2, k, b, O1M, OM, O1M1')


def eq_to_lambda_OO2(*args):
  lambdas = []
  for func in args:
    lambdas.append(lambdify([(px1, py1, px2, py2)], func))

  return lambdas

def eq_to_lambda_O1M(*args):
  lambdas = []
  for func in args:
    lambdas.append(lambdify([(k, b, O1M)], func))

  return lambdas


func_phi_ = lambdify(t, 0.2 * (t**3) + t)

func_ang_vel = 0.6 * (t**2) + 1
func_vel_O = func_ang_vel * O1O

# Gives the length of the OM
func_len_OM = 5 * sqrt(2) * (t**2 + t)
len_OM_ = lambdify(t, func_len_OM)

# Gives the length of O1M
func_len_O1M = sqrt(O1O**2 + OM**2 - 2 * O1O * OM * cos(alpha))
len_O1M_ = lambdify(OM, func_len_O1M)

# Finds coordinates of point O
func_x_O = O1O*cos(phi)
func_y_O = O1O*sin(phi)
x_O_, y_O_ = lambdify(phi, func_x_O), lambdify(phi, func_y_O)

# Finds coordinates of point O2
func_x_O2 = O1O*cos(phi + np.radians(90))
func_y_O2 = O1O*sin(phi + np.radians(90))
x_O2_, y_O2_ = lambdify(phi, func_x_O2), lambdify(phi, func_y_O2)

# Finds the components (k and b of equation y = kx + b) of the line using points O and O2
solve_eq_OO2 = solve([py1 - k_OO2 * px1 - b_OO2, py2 - k_OO2 * px2 - b_OO2], [k_OO2, b_OO2], dict=True)
k_solved_OO2 = solve_eq_OO2[0][k_OO2]
b_solved_OO2 = solve_eq_OO2[0][b_OO2]

k_OO2_func, b_OO2_func = eq_to_lambda_OO2(k_solved_OO2, b_solved_OO2)

# Finds the coordinates of point M
coord_M = solve([x_M ** 2 + y_M ** 2 - O1M ** 2, y_M - k * x_M - b], [x_M, y_M], dict=True)

x_M_0 = coord_M[0][x_M]
y_M_0 = coord_M[0][y_M]
x_M_1 = coord_M[1][x_M]
y_M_1 = coord_M[1][y_M]
x_M0_, y_M0_ = eq_to_lambda_O1M(x_M_0, y_M_0)
x_M1_, y_M1_ = eq_to_lambda_O1M(x_M_1, y_M_1)


In [7]:
# Set up the figure and axis
fig, ax = plt.subplots()
ax.set_xlim(-70, 70)
ax.set_ylim(-70, 70)

lineO1O, = ax.plot([], [], 'r', lw = 2)
lineO1O2, = ax.plot([], [], 'm', lw = 2)
lineOO2, = ax.plot([], [], 'g--', lw = 2)
lineO1M, = ax.plot([], [], 'b--', lw = 2)
traj, = ax.plot([], [], 'g--', lw = 2)

pointM, = ax.plot([], [], 'bo', markersize = 5)
pointO, = ax.plot([], [], 'ro', markersize = 5)
pointO2, = ax.plot([], [], 'mo', markersize = 5)

def update(frame):
    phi = func_phi_(t_values[frame])
    x_O, y_O = x_O_(phi), y_O_(phi)
    pointO.set_data(x_O, y_O)
    
    x_O2, y_O2 = x_O2_(phi), y_O2_(phi)
    pointO2.set_data(x_O2, y_O2)
    
    k = k_OO2_func((x_O, y_O, x_O2, y_O2))
    b = b_OO2_func((x_O, y_O, x_O2, y_O2))
    OM = len_OM_(t_values[frame])
    O1M = len_O1M_(OM)    
    
    # Comment this and uncomment the next part to correct the simulation
    x_M, y_M = x_M0_((k, b, O1M)), y_M0_((k, b, O1M))
    
    # With this commented code the simulation is correct, but without there are some troubles because of trying to divide by 0 
    
    # if 3 * np.pi/4 <= phi <= 7*np.pi/4:
    #     if t_values[frame] < 2:
    #         x_M, y_M = x_M1_((k, b, O1M)), y_M1_((k, b, O1M))
    #     else:
    #         x_M, y_M = x_M0_((k, b, O1M)), y_M0_((k, b, O1M))
    # else:
    #     if t_values[frame] > 2:
    #         x_M, y_M = x_M1_((k, b, O1M)), y_M1_((k, b, O1M))
    #     else:
    #         x_M, y_M = x_M0_((k, b, O1M)), y_M0_((k, b, O1M))
    
    
    
    lineO1O.set_data([0, x_O], [0, y_O])
    lineO1O2.set_data([0, x_O2], [0, y_O2])
    lineOO2.set_data([x_O, x_O2], [y_O, y_O2])
    lineO1M.set_data([0, x_M], [0, y_M])
    traj.set_data(np.append(traj.get_xdata(), x_M), np.append(traj.get_ydata(), y_M))
    
    pointM.set_data((x_M, y_M))
    
    return ...

plt.title('Triangle rotates')
plt.xlabel('X-axis')
plt.ylabel('Y-axis')
plt.grid(True)
plt.gca().set_aspect('equal', adjustable='box')
plt.legend()    
    
ani = animation.FuncAnimation(fig, update, frames=num_frames, interval=40)


plt.gca().set_aspect('equal', adjustable='box')    
plt.grid(True)
# ani.save("task2_sim.gif")
display(HTML(ani.to_jshtml()))
plt.close(fig)


No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
C:\Users\User\AppData\Local\Temp\ipykernel_272\2619126928.py:19: MatplotlibDeprecationWarning: Setting data with a non sequence type is deprecated since 3.7 and will be remove two minor releases later
  pointO.set_data(x_O, y_O)
C:\Users\User\AppData\Local\Temp\ipykernel_272\2619126928.py:22: MatplotlibDeprecationWarning: Setting data with a non sequence type is deprecated since 3.7 and will be remove two minor releases later
  pointO2.set_data(x_O2, y_O2)
C:\Users\User\AppData\Local\Temp\ipykernel_272\2619126928.py:53: MatplotlibDeprecationWarning: Setting data with a non sequence type is deprecated since 3.7 and will be remove two minor releases later
  pointM.set_data((x_M, y_M))
